<a href="https://colab.research.google.com/github/agorla23/projectcentral/blob/main/NBA_Neural_Network_Prediction.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install selenium
!apt-get update
!apt install chromium-chromedriver
!cp /usr/lib/chromium-browser/chromedriver /usr/bin
!pip install webdriver_manager

In [ ]:


from selenium import webdriver
from webdriver_manager.chrome import ChromeDriverManager
driver = webdriver.Chrome(ChromeDriverManager().install())


ModuleNotFoundError: No module named 'selenium'

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import os
import re
import json
from urllib.parse import urljoin
import time
import random
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense


In [ ]:
f(11)

11

In [ ]:
google_drive_dir = "/content/drive/MyDrive/2023 summer project"

In [ ]:
import requests
from bs4 import BeautifulSoup
import time
import csv
import pandas as pd
import random

BASE_URL = "https://www.basketball-reference.com"
PLAYERS_URL = BASE_URL + "/players/"

user_agents = [
    'Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:91.0) Gecko/20100101 Firefox/91.0',
    'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/92.0.4515.159 Safari/537.36',
    'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/605.1.15 (KHTML, like Gecko) Version/14.1.2 Safari/605.1.15'

]

def fetch_url(url):
    MAX_RETRIES = 5
    for attempt in range(MAX_RETRIES):
        headers = {
            'User-Agent': random.choice(user_agents)
        }
        response = requests.get(url, headers=headers)

        if response.status_code == 200:
            return response
        elif response.status_code == 429:
            print(f"Rate limited. Retrying in a few seconds...")
            time.sleep(random.uniform(10, 15))
        else:
            print(f"Failed to retrieve the webpage. Status code: {response.status_code}")
            time.sleep(random.uniform(2, 5))
    return None

all_players = []
for letter in 'abcdefghijklmnopqrstuvwxyz':
    all_players.extend(get_players_for_letter(letter))
    time.sleep(random.uniform(2, 5))

processed_players = set()
for player in all_players:
    if player['name'] in processed_players:
        continue
    for year in range(1947, 2023):
        game_log = fetch_game_log(player, year)
        if game_log is not None:
            filename = f"{player['name'].replace(' ', '_')}_{year}_gamelogs.csv"
            game_log.to_csv(filename, index=False)
        time.sleep(random.uniform(1, 3))
    processed_players.add(player['name'])


In [ ]:
import requests
from bs4 import BeautifulSoup
import time
import pandas as pd
import random

BASE_URL = "https://www.basketball-reference.com"
PLAYERS_URL = BASE_URL + "/players/"

google_drive_dir = "/content/drive/MyDrive/2023 summer project"
user_agents = [
    'Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:91.0) Gecko/20100101 Firefox/91.0',
    'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/92.0.4515.159 Safari/537.36',
    'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/605.1.15 (KHTML, like Gecko) Version/14.1.2 Safari/605.1.15'
]

def fetch_url(url):
    MAX_RETRIES = 5
    for attempt in range(MAX_RETRIES):
        headers = {
            'User-Agent': random.choice(user_agents)
        }
        response = requests.get(url, headers=headers)

        if response.status_code == 200:
            return response
        elif response.status_code == 429:
            print(f"Rate limited on attempt {attempt+1}. Retrying in a few seconds...")
            time.sleep(random.uniform(10, 15))
        else:
            print(f"Failed to retrieve the webpage on attempt {attempt+1}. Status code: {response.status_code}")
            time.sleep(random.uniform(2, 5))
    return None

def get_players_for_letter(letter):
    url = PLAYERS_URL + letter + "/"
    response = fetch_url(url)

    if response is None:
        return []

    soup = BeautifulSoup(response.text, 'html.parser')
    player_links = soup.select("th[data-stat='player'] a")
    players = [{"name": link.text, "link": link['href']} for link in player_links]
    return players

def fetch_game_log(player, year):
    game_log_url = BASE_URL + player['link'].replace('.html', f'/gamelog/{year}')
    response = fetch_url(game_log_url)

    if response is None:
        return None

    soup = BeautifulSoup(response.text, 'html.parser')
    table = soup.select_one("#pgl_basic")

    if table:
        headers = [th.text for th in table.thead.find_all("th")]
        rows = table.tbody.find_all("tr")
        data = [[td.text for td in row.find_all("td")] for row in rows]

        if len(headers) - 1 != len(data[0]):
            print(f"Column mismatch for {player['name']} in {year}. Skipping...")
            return None

        df = pd.DataFrame(data, columns=headers[1:])
        return df
    return None

all_players = []
for letter in 'abcdefghijklmnopqrstuvwxyz':
    all_players.extend(get_players_for_letter(letter))
    time.sleep(random.uniform(2, 5))

print(f"Total players fetched: {len(all_players)}")

resume_from = "Justin James"
resume_scraping = False

print("Entering the game logs loop...")

players_processed_after_resume = 0
processed_players = set()

for player in all_players:
    if not resume_scraping:
        if player['name'] == resume_from:
            print(f"Resuming scraping from player: {player['name']}")
            resume_scraping = True
            continue
        else:
            continue

    print(f"Fetching game logs for {player['name']}...")
    players_processed_after_resume += 1

    try:
        for year in range(1947, 2023):
            game_log = fetch_game_log(player, year)
            if game_log is not None:
                filename = f"{google_drive_dir}/{player['name'].replace(' ', '_')}_{year}_gamelogs.csv"
                game_log.to_csv(filename, index=False)
                print(f"Saved game logs for {player['name']} for the year {year}.")
            time.sleep(random.uniform(1, 3))
    except Exception as e:
        print(f"An error occurred while processing {player['name']}: {e}")

    processed_players.add(player['name'])
    print(f"Finished processing {player['name']}.\n")

print(f"Total players processed after {resume_from}: {players_processed_after_resume}")
print("Finished processing all players.")







Total players fetched: 5143
Entering the game logs loop...
Resuming scraping from player: Justin James
Fetching game logs for LeBron James...
Saved game logs for LeBron James for the year 2004.
Saved game logs for LeBron James for the year 2005.
Saved game logs for LeBron James for the year 2006.
Saved game logs for LeBron James for the year 2007.
Saved game logs for LeBron James for the year 2008.
Saved game logs for LeBron James for the year 2009.
Saved game logs for LeBron James for the year 2010.
Saved game logs for LeBron James for the year 2011.
Saved game logs for LeBron James for the year 2012.
Saved game logs for LeBron James for the year 2013.
Saved game logs for LeBron James for the year 2014.
Saved game logs for LeBron James for the year 2015.
Saved game logs for LeBron James for the year 2016.
Saved game logs for LeBron James for the year 2017.
Saved game logs for LeBron James for the year 2018.
Saved game logs for LeBron James for the year 2019.
Saved game logs for LeBron

KeyboardInterrupt: ignored

In [ ]:

for idx, player in enumerate(all_players):
    if "" in player['name']:
        start_idx = max(0, idx - 5)
        end_idx = min(len(all_players), idx + 6)
        for i in range(start_idx, end_idx):
            print(all_players[i]['name'])
        break

print("Entering the game logs loop...")


Nick Anderson
Richard Anderson
Ron Anderson
Ryan Anderson
Shandon Anderson
Willie Anderson
Wally Anderzunas
Martynas Andriuškevičius
Don Anielak
Ike Anigbogu
Michael Ansley
Entering the game logs loop...


In [ ]:
import pandas as pd

google_drive_dir = "/content/drive/MyDrive/2023 summer project"
player_name = "Michael Jordan"
year =  1993
filename = f"/content/drive/MyDrive/2023 player_gamelogs/{player_name}_{year}_gamelogs.csv"
df = pd.read_csv(filename)
df







FileNotFoundError: ignored

In [ ]:
import os
base_dir = "/content/drive/MyDrive/2023 summer project"
gamelogs_dir = os.path.join(base_dir, "player_gamelogs")
player_name = "LeBron_James"
year = 2018
filename = f"{player_name}_{year}_gamelogs.csv"
if filename in os.listdir(gamelogs_dir):
    print(f"The file '{filename}' is in the directory.")
else:
    print(f"The file '{filename}' is not in the directory.")



The file 'LeBron_James_2018_gamelogs.csv' is in the directory.


In [ ]:
!ls "/content/drive/MyDrive/2023 summer project"


Abdul_Jeelani_1980_gamelogs.csv       Kosta_Koufos_2012_gamelogs.csv
Abdul_Jeelani_1981_gamelogs.csv       Kosta_Koufos_2013_gamelogs.csv
Alexander_Johnson_2007_gamelogs.csv   Kosta_Koufos_2014_gamelogs.csv
Alexander_Johnson_2008_gamelogs.csv   Kosta_Koufos_2015_gamelogs.csv
Alize_Johnson_2022_gamelogs.csv       Kosta_Koufos_2016_gamelogs.csv
Al_Jefferson_2005_gamelogs.csv	      Kosta_Koufos_2017_gamelogs.csv
Al_Jefferson_2006_gamelogs.csv	      Kosta_Koufos_2018_gamelogs.csv
Al_Jefferson_2007_gamelogs.csv	      Kyle_Korver_2004_gamelogs.csv
Al_Jefferson_2008_gamelogs.csv	      Kyle_Korver_2005_gamelogs.csv
Al_Jefferson_2009_gamelogs.csv	      Kyle_Korver_2006_gamelogs.csv
Al_Jefferson_2010_gamelogs.csv	      Kyle_Korver_2007_gamelogs.csv
Al_Jefferson_2011_gamelogs.csv	      Kyle_Korver_2008_gamelogs.csv
Al_Jefferson_2012_gamelogs.csv	      Kyle_Korver_2009_gamelogs.csv
Al_Jefferson_2013_gamelogs.csv	      Kyle_Korver_2011_gamelogs.csv
Al_Jefferson_2014_gamelogs.csv	      Kyle_Korver_2

In [ ]:
def random_sleep(minimum=1, maximum=10):

    sleep_time = random.uniform(minimum, maximum)
    time.sleep(sleep_time)

In [ ]:
def save_table_as_csv(table, player_dir, table_name, player_name):
    df = pd.read_html(str(table))[0]
    df['Player_Name'] = player_name

    caption_tag = table.find('caption')

    filename = table_name + '.csv'
    save_dir = os.path.join(google_drive_dir, player_dir)
    os.makedirs(save_dir, exist_ok=True)
    file_handle = os.path.join(save_dir, filename)
    df.to_csv(file_handle, index=False)
    print(f"Saved {file_handle}...")


In [ ]:
def extract_player_name(html_body):
  soup = BeautifulSoup(html_body, 'html.parser')

  player_name = soup.select_one('.breadcrumbs strong').text

  return player_name





In [ ]:
url="https://www.basketball-reference.com/players/a/abdulka01.html"
response = requests.get(url)
extract_player_name(response.text)

'Kareem Abdul-Jabbar'

In [ ]:
def scrape_page(url):
    response = requests.get(url)
    soup = BeautifulSoup(response.text, 'html.parser')

    subpages = []
    try:
        if re.search(r'players/[a-z]/?$', url):
            for player_page in soup.find_all('div', id='div_players'):
              for player_table in player_page.find_all('table'):
                players = player_table.find_all('th', {'data-stat': 'player'})
                for player in players:
                    player_link = player.find('a')
                    if player_link:
                        subpages.append('https://www.basketball-reference.com' + player_link.get('href'))
        elif url.split('/')[-3] == 'players' and re.search(r'players/[a-z]/', url):
            if url.endswith("html"):
              player_name_dir = url.split('.')[-2].split('/')[-1]
            else:
              player_name_dir = url.split('/')[-1]

            player_name = extract_player_name(response.text)
            player_dir = os.path.join('players', player_name_dir)
            table_containers = soup.find_all('div', class_='table_container')
            for i, table_container in enumerate(table_containers):
                tables = table_container.find_all('table')
                for table in tables:
                    save_table_as_csv(table, player_dir, table.get('id', table.caption), player_name)  # Pass player_name

        return subpages
    except Exception as ex:
        print(f"Received exception on url {url}")
        raise(ex)




In [ ]:
def scrape_website(base_url):
    player_page = urljoin(base_url, 'players')
    response = requests.get(player_page)
    soup = BeautifulSoup(response.text, 'html.parser')
    player_list_items = soup.find('ul', class_='page_index').find_all('li')
    links = [player_page]
    for li in player_list_items:
        player_links = li.find_all('a', href=True)
        for link in player_links:
          links.append(urljoin(base_url, link['href']))

    pages_to_scrape = {page: "Not-checked" for page in links}

    while "Not-checked" in pages_to_scrape.values():

        page = next(page for page, status in pages_to_scrape.items() if status == "Not-checked")

        subpages = scrape_page(page)

        for subpage in subpages:
            if subpage not in pages_to_scrape:
                pages_to_scrape[subpage] = "Not-checked"

        pages_to_scrape[page] = "Checked"
        random_sleep()

    with open("scraped_pages.json", "w") as f:
        json.dump(pages_to_scrape, f)



In [ ]:
base_url = 'https://www.basketball-reference.com/'
scrape_website(base_url)

Saved /content/drive/MyDrive/2023 summer project/players/abdulka01/per_game.csv...
Saved /content/drive/MyDrive/2023 summer project/players/abdulka01/playoffs_per_game.csv...
Saved /content/drive/MyDrive/2023 summer project/players/abdulka01/stathead_insights.csv...
Saved /content/drive/MyDrive/2023 summer project/players/abdulka01/totals.csv...
Saved /content/drive/MyDrive/2023 summer project/players/abdulka01/playoffs_totals.csv...
Saved /content/drive/MyDrive/2023 summer project/players/abdulka01/advanced.csv...
Saved /content/drive/MyDrive/2023 summer project/players/abdulka01/playoffs_advanced.csv...
Saved /content/drive/MyDrive/2023 summer project/players/allenra02/per_game.csv...
Saved /content/drive/MyDrive/2023 summer project/players/allenra02/playoffs_per_game.csv...
Saved /content/drive/MyDrive/2023 summer project/players/allenra02/stathead_insights.csv...
Saved /content/drive/MyDrive/2023 summer project/players/allenra02/totals.csv...
Saved /content/drive/MyDrive/2023 summe

KeyboardInterrupt: ignored

In [ ]:
print(seasons_links)

[]


In [ ]:
import pandas as pd
import os
from collections import defaultdict
dataframes = []
organized_dataframes = defaultdict(list)
directory = '/content/drive/MyDrive/2023 summer project/players'
for root, dirs, files in os.walk(directory):
    for file in files:
        if file.endswith('.csv'):
            filepath = os.path.join(root, file)
            df = pd.read_csv(filepath)
            df['player'] = os.path.basename(root)
            organized_dataframes[file].append(df)
for key,value in organized_dataframes.items():
    all_data = pd.concat(value)





In [ ]:
import pandas as pd
import os
from collections import defaultdict
import time

organized_dataframes = defaultdict(list)
directory = '/content/drive/MyDrive/2023 summer project/players'

start_time = time.time()
for root, dirs, files in os.walk(directory):
    for file in files:
        if file.endswith('.csv'):
            filepath = os.path.join(root, file)
            print(f"Processing {filepath}...")
            file_start_time = time.time()
            df = pd.read_csv(filepath, error_bad_lines=False)
            print(f"Processed {filepath} in {time.time() - file_start_time} seconds.")
            df['player'] = os.path.basename(root)
            organized_dataframes[file].append(df)
print(f"Finished reading files in {time.time() - start_time} seconds.")

all_data = {}
for key,value in organized_dataframes.items():
    all_data[key] = pd.concat(value)

Processing /content/drive/MyDrive/2023 summer project/players/butleca01/per_game.csv...


<ipython-input-2-d0c975be91a5>:16: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  df = pd.read_csv(filepath, error_bad_lines=False)


Processed /content/drive/MyDrive/2023 summer project/players/butleca01/per_game.csv in 0.23870635032653809 seconds.
Processing /content/drive/MyDrive/2023 summer project/players/butleca01/playoffs_totals.csv...


<ipython-input-2-d0c975be91a5>:16: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  df = pd.read_csv(filepath, error_bad_lines=False)


Processed /content/drive/MyDrive/2023 summer project/players/butleca01/playoffs_totals.csv in 0.2977793216705322 seconds.
Processing /content/drive/MyDrive/2023 summer project/players/butleca01/playoffs_per_game.csv...


...

Processed /content/drive/MyDrive/2023 summer project/players/butleal01/advanced.csv in 0.22810101509094238 seconds.
Processing /content/drive/MyDrive/2023 summer project/players/butleal01/per_game.csv...


<ipython-input-2-d0c975be91a5>:16: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  df = pd.read_csv(filepath, error_bad_lines=False)


Processed /content/drive/MyDrive/2023 summer project/players/butleal01/per_game.csv in 0.3269767761230469 seconds.
Processing /content/drive/MyDrive/2023 summer project/players/butleal01/stathead_insights.csv...
Processed /content/drive/MyDrive/2023 summer project/players/butleal01/stathead_insights.csv in 0.15561723709106445 seconds.
Processing /content/drive/MyDrive/2023 summer project/players/butleal01/totals.csv...


<ipython-input-2-d0c975be91a5>:16: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  df = pd.read_csv(filepath, error_bad_lines=False)
<ipython-input-2-d0c975be91a5>:16: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  df = pd.read_csv(filepath, error_bad_lines=False)


Processed /content/drive/MyDrive/2023 summer project/players/butleal01/totals.csv in 0.17540431022644043 seconds.
Finished reading files in 2122.23752450943 seconds.


In [ ]:
all_data_dict = all_data.to_dict(orient='records')
all_data_dict

for Player_Name in all_data_dict:
    print(Player_Name)


AttributeError: ignored

In [ ]:
all_data_dict

NameError: ignored

In [ ]:
save_dir = "/content/drive/MyDrive/2023 summer project/processed_data"
os.makedirs(save_dir, exist_ok=True)
for key, value in all_data.items():
  value.to_csv(os.path.join(save_dir, key))

NameError: ignored

In [ ]:
save_dir = "/content/drive/MyDrive/2023 summer project/processed_data"
per_game_all_data = pd.read_csv(os.path.join(save_dir, "per_game.csv"))

In [ ]:
per_game_all_data

Unnamed: 0     Season   Age   Tm   Lg  Pos      G    GS    MP   FG  \
0               0    2002-03  22.0  MIA  NBA   SF   78.0  78.0  36.6  5.5   
1               1    2003-04  23.0  MIA  NBA   SF   68.0  56.0  29.9  3.5   
2               2    2004-05  24.0  LAL  NBA   SF   77.0  77.0  35.7  5.7   
3               3    2005-06  25.0  WAS  NBA   SF   75.0  54.0  36.1  6.6   
4               4    2006-07  26.0  WAS  NBA   SF   63.0  63.0  39.3  7.2   
...           ...        ...   ...  ...  ...  ...    ...   ...   ...  ...   
20000           6     Career   NaN  NaN  NBA  NaN  234.0   NaN  21.6  4.0   
20001           7        NaN   NaN  NaN  NaN  NaN    NaN   NaN   NaN  NaN   
20002           8  3 seasons   NaN  NYK  NBA  NaN  204.0   NaN  23.7  4.4   
20003           9   1 season   NaN  BAL  NBA  NaN   25.0   NaN   6.9  1.0   
20004          10   1 season   NaN  BOS  NBA  NaN    5.0   NaN   9.4  2.6   

       ...  DRB  TRB  AST  STL  BLK  TOV   PF   PTS   Player_Name     player  
0      ...  3.4  5.1  2.7  1.8  0.4  2.5  2.9  15.4  Caron Butler  butleca01  
1      ...  3.4  4.8  1.9  1.1  0.2  1.3  2.4   9.2  Caron Butler  butleca01  
2      ...  3.9  5.8  1.9  1.4  0.3  1.6  2.8  15.5  Caron Butler  butleca01  
3      ...  4.7  6.2  2.5  1.7  0.2  2.3  3.2  17.6  Caron Butler  butleca01  
4      ...  5.1  7.4  3.7  2.1  0.3  2.9  3.0  19.1  Caron Butler  butleca01  
...    ...  ...  ...  ...  ...  ...  ...  ...   ...           ...        ...  
20000  ...  NaN  3.0  2.3  NaN  NaN  NaN  2.1   9.8     Al Butler  butleal01  
20001  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN   NaN     Al Butler  butleal01  
20002  ...  NaN  3.2  2.5  NaN  NaN  NaN  2.3  10.7     Al Butler  butleal01  
20003  ...  NaN  0.8  0.5  NaN  NaN  NaN  1.0   2.4     Al Butler  butleal01  
20004  ...  NaN  2.6  0.8  NaN  NaN  NaN  1.8   6.2     Al Butler  butleal01  

[20005 rows x 33 columns]

In [ ]:
per_game_all_data.rename(columns={'Player_Name': 'PlayerName'}, inplace=True)


In [ ]:
per_game_all_data

Empty DataFrame
Columns: [Unnamed: 0, Season, Age, Tm, Lg, Pos, G, GS, MP, FG, FGA, FG%, 3P, 3PA, 3P%, 2P, 2PA, 2P%, eFG%, FT, FTA, FT%, ORB, DRB, TRB, AST, STL, BLK, TOV, PF, PTS, PlayerName, player]
Index: []

[0 rows x 33 columns]

In [ ]:
per_game_all_data = per_game_all_data[per_game_all_data['Season'].str.match(r'^\d{4}-\d{2}$', na=False)]
per_game_all_data

NameError: ignored

In [ ]:
per_game_all_data.sample()

Unnamed: 0   Season   Age   Tm   Lg Pos     G   GS    MP   FG  ...  DRB  \
697           4  2010-11  26.0  TOT  NBA  SF  27.0  1.0  12.4  1.7  ...  1.3   

     TRB  AST  STL  BLK  TOV   PF  PTS    Player_Name     player  
697  1.8  0.4  0.4  0.2  0.6  1.2  4.7  Rodney Carney  carnero01  

[1 rows x 33 columns]

In [ ]:

categorical_columns = ['Tm', 'Lg', 'Pos']


encoded_df = pd.get_dummies(per_game_all_data, columns=categorical_columns)

encoded_df
encoded_per_game_all_data = pd.get_dummies(per_game_all_data, columns=categorical_columns)
encoded_per_game_all_data

Unnamed: 0     Season   Age      G    GS    MP   FG   FGA    FG%   3P  \
0               0    2002-03  22.0   78.0  78.0  36.6  5.5  13.2  0.416  0.4   
1               1    2003-04  23.0   68.0  56.0  29.9  3.5   9.3   0.38  0.1   
2               2    2004-05  24.0   77.0  77.0  35.7  5.7  12.9  0.445  0.5   
3               3    2005-06  25.0   75.0  54.0  36.1  6.6  14.5  0.455  0.5   
4               4    2006-07  26.0   63.0  63.0  39.3  7.2  15.5  0.463  0.3   
...           ...        ...   ...    ...   ...   ...  ...   ...    ...  ...   
20000           6     Career   NaN  234.0   NaN  21.6  4.0   9.1  0.439  NaN   
20001           7        NaN   NaN    NaN   NaN   NaN  NaN   NaN    NaN  NaN   
20002           8  3 seasons   NaN  204.0   NaN  23.7  4.4   9.9  0.443  NaN   
20003           9   1 season   NaN   25.0   NaN   6.9  1.0   2.9  0.329  NaN   
20004          10   1 season   NaN    5.0   NaN   9.4  2.6   5.8  0.448  NaN   

       ... player_youngni01 player_youngsa01 player_youngth01  \
0      ...                0                0                0   
1      ...                0                0                0   
2      ...                0                0                0   
3      ...                0                0                0   
4      ...                0                0                0   
...    ...              ...              ...              ...   
20000  ...                0                0                0   
20001  ...                0                0                0   
20002  ...                0                0                0   
20003  ...                0                0                0   
20004  ...                0                0                0   

      player_youngtr01 player_zasloma01 player_zawolze01 player_zelleco01  \
0                    0                0                0                0   
1                    0                0                0                0   
2                    0                0                0                0   
3                    0                0                0                0   
4                    0                0                0                0   
...                ...              ...              ...              ...   
20000                0                0                0                0   
20001                0                0                0                0   
20002                0                0                0                0   
20003                0                0                0                0   
20004                0                0                0                0   

      player_zelleha01 player_zellety01 player_zubaciv01  
0                    0                0                0  
1                    0                0                0  
2                    0                0                0  
3                    0                0                0  
4                    0                0                0  
...                ...              ...              ...  
20000                0                0                0  
20001                0                0                0  
20002                0                0                0  
20003                0                0                0  
20004                0                0                0  

[20005 rows x 4158 columns]

In [ ]:
model = Sequential()


In [ ]:
import os
import shutil

source_directory = "/content/drive/MyDrive/2023 summer project"

player_gamelogs_directory = os.path.join(source_directory, "player_gamelogs")
os.makedirs(player_gamelogs_directory, exist_ok=True)

file_list = os.listdir(source_directory)

for filename in file_list:
    if filename.endswith("_gamelogs.csv"):
        source_path = os.path.join(source_directory, filename)
        output_path = os.path.join(player_gamelogs_directory, filename)

        shutil.move(source_path, output_path)
        print(f"Moved {filename} to {player_gamelogs_directory}")

print(f"All game log files have been moved to the {player_gamelogs_directory} directory.")


Moved Bernard_King_1983_gamelogs.csv to /content/drive/MyDrive/2023 summer project/player_gamelogs
Moved Bernard_King_1984_gamelogs.csv to /content/drive/MyDrive/2023 summer project/player_gamelogs
Moved Bernard_King_1985_gamelogs.csv to /content/drive/MyDrive/2023 summer project/player_gamelogs
Moved Bernard_King_1987_gamelogs.csv to /content/drive/MyDrive/2023 summer project/player_gamelogs
Moved Bernard_King_1988_gamelogs.csv to /content/drive/MyDrive/2023 summer project/player_gamelogs
Moved Bernard_King_1989_gamelogs.csv to /content/drive/MyDrive/2023 summer project/player_gamelogs
Moved Bernard_King_1990_gamelogs.csv to /content/drive/MyDrive/2023 summer project/player_gamelogs
Moved Bernard_King_1991_gamelogs.csv to /content/drive/MyDrive/2023 summer project/player_gamelogs
Moved Bernard_King_1993_gamelogs.csv to /content/drive/MyDrive/2023 summer project/player_gamelogs
Moved Chris_King_1994_gamelogs.csv to /content/drive/MyDrive/2023 summer project/player_gamelogs
Moved Chris_

In [ ]:
import os
directory_path = "/content/drive/MyDrive/2023 summer project/player_gamelogs"
files_in_directory = os.listdir(directory_path)
num_files = len(files_in_directory)
print(f"Number of files in the directory: {num_files}")


Number of files in the directory: 18872


In [ ]:
import os
import pandas as pd
csv_directory = "/content/drive/MyDrive/2023 summer project/player_gamelogs"
dfs = []
for csv_file in os.listdir(csv_directory):
    if not csv_file.endswith(".csv") or csv_file == "combined_gamelogs.csv":
        continue
    print(f"Reading {csv_file}...")
    parts = csv_file.split("_")
    if len(parts) < 4 or not parts[-1].endswith(".csv"):
        print(f"Skipping {csv_file} as it doesn't match the expected filename pattern.")
        continue

    player_name = " ".join(parts[:-2])

    try:
        year = int(parts[-2])
    except ValueError:
        print(f"Skipping {csv_file} due to an invalid year in the filename.")
        continue
    csv_path = os.path.join(csv_directory, csv_file)
    df = pd.read_csv(csv_path)
    df['PlayerName'] = player_name
    df['Year'] = year

    dfs.append(df)
combined_df = pd.concat(dfs, ignore_index=True)

combined_df.to_csv("/content/drive/MyDrive/2023 summer project/All_combined_gamelogs.csv", index=False)

print("All CSV files have been combined into one dataset.")




Streaming output truncated to the last 5000 lines.
Reading Dorian_Finney-Smith_2019_gamelogs.csv...
Reading Dorian_Finney-Smith_2020_gamelogs.csv...
Reading Dorian_Finney-Smith_2021_gamelogs.csv...
Reading Dorian_Finney-Smith_2022_gamelogs.csv...
Reading Matt_Fish_1995_gamelogs.csv...
Reading Matt_Fish_1996_gamelogs.csv...
Reading Derek_Fisher_1997_gamelogs.csv...
Reading Derek_Fisher_1998_gamelogs.csv...
Reading Derek_Fisher_1999_gamelogs.csv...
Reading Derek_Fisher_2000_gamelogs.csv...
Reading Derek_Fisher_2001_gamelogs.csv...
Reading Derek_Fisher_2002_gamelogs.csv...
Reading Derek_Fisher_2003_gamelogs.csv...
Reading Derek_Fisher_2004_gamelogs.csv...
Reading Derek_Fisher_2005_gamelogs.csv...
Reading Derek_Fisher_2006_gamelogs.csv...
Reading Derek_Fisher_2007_gamelogs.csv...
Reading Derek_Fisher_2008_gamelogs.csv...
Reading Derek_Fisher_2009_gamelogs.csv...
Reading Derek_Fisher_2010_gamelogs.csv...
Reading Derek_Fisher_2011_gamelogs.csv...
Reading Derek_Fisher_2012_gamelogs.csv...
Rea

In [ ]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import time
import os

BASE_URL = 'https://www.basketball-reference.com'
team_urls = ['/teams/ATL/', '/teams/BOS/', '/teams/CHA/', '/teams/CHI/', '/teams/CLE/', '/teams/DAL/', '/teams/DEN/', '/teams/DET/', '/teams/GSW/', '/teams/HOU/', '/teams/IND/', '/teams/LAC/', '/teams/LAL/', '/teams/MEM/', '/teams/MIA/', '/teams/MIL/', '/teams/MIN/', '/teams/NOP/', '/teams/NYK/', '/teams/OKC/', '/teams/ORL/', '/teams/PHI/', '/teams/PHO/', '/teams/POR/', '/teams/SAC/', '/teams/SAS/', '/teams/TOR/', '/teams/UTA/', '/teams/WAS/']

google_drive_dir = "/content/drive/MyDrive/2023 summer project"

def save_table_as_csv(table, team_dir):
    df = pd.read_html(str(table))[0]

    caption_tag = table.find('caption')
    if caption_tag:
        table_name = caption_tag.get_text().strip().replace(' ', '_').replace('.', '')
    else:
        table_name = "table"

    filename = table_name + '.csv'

    save_dir = os.path.join(google_drive_dir, team_dir)
    os.makedirs(save_dir, exist_ok=True)
    file_handle = os.path.join(save_dir, filename)

    df.to_csv(file_handle, index=False)
    print(f"Saved {file_handle}...")

def get_gamelog_for_team(team_url, year):
    print(f"Attempting to extract data for {team_url} for the {year}-{year+1} season")
    url = BASE_URL + team_url + str(year) + "/gamelog/"

    try:
        response = requests.get(url)
        response.raise_for_status()

        soup = BeautifulSoup(response.text, 'html.parser')
        table = soup.find('table', {'id': 'tgl_basic'})
        if not table:
            print(f"No table found for URL: {url}")
            return None

        df = pd.read_html(str(table))[0]
        df['Season'] = f"{year}-{year+1}"

        # Save the dataframe to CSV
        team_name = team_url.split("/")[2]
        save_dir = f"{team_name}_{year}-{year+1}"
        save_table_as_csv(table, save_dir)

        return df

    except requests.RequestException as e:
        print(f"Error fetching {url}. Error: {e}")
        return None

all_dataframes = []

for year in range(2003, 2024):
    for team_url in team_urls:
        df = get_gamelog_for_team(team_url, year)
        if df is not None:
            all_dataframes.append(df)
        time.sleep(2)

combined_df = pd.concat(all_dataframes, ignore_index=True)
print(combined_df)

Processing /content/drive/MyDrive/2023 summer project/players/casspom01/totals.csv...


<ipython-input-2-9733de18a90d>:16: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  df = pd.read_csv(filepath, error_bad_lines=False)


Processed /content/drive/MyDrive/2023 summer project/players/casspom01/totals.csv in 0.28165102005004883 seconds.
Processing /content/drive/MyDrive/2023 summer project/players/casspom01/stathead_insights.csv...


<ipython-input-2-9733de18a90d>:16: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  df = pd.read_csv(filepath, error_bad_lines=False)


Processed /content/drive/MyDrive/2023 summer project/players/casspom01/stathead_insights.csv in 0.2503218650817871 seconds.
Processing /content/drive/MyDrive/2023 summer project/players/casspom01/per_game.csv...


...

Processed /content/drive/MyDrive/2023 summer project/players/cluggbo01/per_game.csv in 0.29531264305114746 seconds.
Processing /content/drive/MyDrive/2023 summer project/players/cluggbo01/stathead_insights.csv...


<ipython-input-2-9733de18a90d>:16: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  df = pd.read_csv(filepath, error_bad_lines=False)


Processed /content/drive/MyDrive/2023 summer project/players/cluggbo01/stathead_insights.csv in 0.2652778625488281 seconds.
Processing /content/drive/MyDrive/2023 summer project/players/cluggbo01/advanced.csv...


<ipython-input-2-9733de18a90d>:16: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  df = pd.read_csv(filepath, error_bad_lines=False)


ParserError: ignored

In [ ]:
save_dir = "/content/drive/MyDrive/2023 summer project/processed_data"
gamelog_data_1 = pd.read_csv(os.path.join(save_dir, "All_combined_gamelogs.csv"))

In [ ]:
save_dir = "/content/drive/MyDrive/2023 summer project/reg_szn"
gamelog_data_1 = pd.read_csv(os.path.join(save_dir, "new_combined_gamelogs.csv"))

In [ ]:
save_dir = "/content/drive/MyDrive/2023 summer project/processed_data"
merged_data_2 = pd.read_csv(os.path.join(save_dir, "merged_data_2.csv"))

In [ ]:
save_dir = "/content/drive/MyDrive/2023 summer project/processed_data"
team_data_1 = pd.read_csv(os.path.join(save_dir, "Team_data.csv"))

In [ ]:
save_dir = "/content/drive/MyDrive/2023 summer project/processed_data"
merged_data = pd.read_csv(os.path.join(save_dir, "stathead_insights.csv"))

In [ ]:

save_dir = "/content/drive/MyDrive/2023 summer project/processed_data"
Position_data = pd.read_csv(os.path.join(save_dir, "Position_data_1.csv"))


In [ ]:

save_dir = "/content/drive/MyDrive/2023 summer project/processed_data"
data.to_csv(os.path.join(save_dir, "RNN_model_data.csv"), index=False)
RNN_data = pd.read_csv(os.path.join(save_dir, "RNN_model_data.csv"))

In [ ]:
save_dir = "/content/drive/MyDrive/2023 summer project/processed_data"
data = pd.read_csv(os.path.join(save_dir, "model_data.csv"))

In [ ]:
save_dir = "/content/drive/MyDrive/2023 summer project/processed_data"
Position_data = pd.read_csv(os.path.join(save_dir, "Position_data.csv"))

In [ ]:
gamelog_data_1

G        Date     Age   Tm       Opp       .1        GS     MP  \
0        1.0  1990-11-11  28-124  MIN  NaN  ORL  W (+27)         0   2:00   
1        2.0  1990-11-15  28-128  MIN    @  DEN  L (-13)         0  15:00   
2        3.0  1990-11-18  28-131  MIN  NaN  UTA   L (-9)         1  25:00   
3        4.0  1990-11-20  28-133  MIN    @  DAL   W (+1)         0   7:00   
4        5.0  1990-11-21  28-134  MIN    @  SAS  L (-14)         0   6:00   
...      ...         ...     ...  ...  ...  ...      ...       ...    ...   
1262760  NaN  2019-04-03  20-326  ORL  NaN  NYK  W (+14)  Inactive    NaN   
1262761  NaN  2019-04-05  20-328  ORL  NaN  ATL  W (+36)  Inactive    NaN   
1262762  NaN         NaN     NaN  NaN  NaN  NaN      NaN       NaN    NaN   
1262763  NaN  2019-04-07  20-330  ORL    @  BOS   W (+8)  Inactive    NaN   
1262764  NaN  2019-04-10  20-333  ORL    @  CHO   W (+8)  Inactive    NaN   

          FG  ...  AST  STL  BLK  TOV   PF  PTS  GmSc    PlayerName  Year  +/-  
0        0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0   0.0  Bob Thornton  1991  NaN  
1        2.0  ...  1.0  0.0  0.0  0.0  2.0  5.0   4.4  Bob Thornton  1991  NaN  
2        0.0  ...  0.0  0.0  0.0  1.0  4.0  2.0  -0.6  Bob Thornton  1991  NaN  
3        0.0  ...  0.0  0.0  0.0  0.0  1.0  0.0  -1.5  Bob Thornton  1991  NaN  
4        1.0  ...  0.0  0.0  0.0  1.0  1.0  2.0   0.9  Bob Thornton  1991  NaN  
...      ...  ...  ...  ...  ...  ...  ...  ...   ...           ...   ...  ...  
1262760  NaN  ...  NaN  NaN  NaN  NaN  NaN  NaN   NaN      Mo Bamba  2019  NaN  
1262761  NaN  ...  NaN  NaN  NaN  NaN  NaN  NaN   NaN      Mo Bamba  2019  NaN  
1262762  NaN  ...  NaN  NaN  NaN  NaN  NaN  NaN   NaN      Mo Bamba  2019  NaN  
1262763  NaN  ...  NaN  NaN  NaN  NaN  NaN  NaN   NaN      Mo Bamba  2019  NaN  
1262764  NaN  ...  NaN  NaN  NaN  NaN  NaN  NaN   NaN      Mo Bamba  2019  NaN  

[1262765 rows x 31 columns]

In [ ]:
import pandas as pd
merged_data['Date'] = pd.to_datetime(merged_data['Date'])

def calculate_season(date):
    if date.month >= 10:
        return f"{date.year}-{date.year + 1}"
    else:
        return f"{date.year - 1}-{date.year}"

merged_data['Season'] = merged_data['Date'].apply(calculate_season)



In [ ]:
data['Date'] = pd.to_datetime(data['Date'])

data.sort_values(by='Date', inplace=True)

In [ ]:
data.rename(columns={'Opp.1': 'Opp_score'}, inplace=True)

In [ ]:
data.rename(columns={'Unnamed: 3_level_1': 'home_or_away'}, inplace=True)


In [ ]:
data

Rk   G       Date W/L  Tm_score  Opposition_score  team_FG  team_FGA  \
18      2   2 2002-10-30   W        95                93       31        86   
3       2   2 2002-10-30   W        98                96       36        84   
22      2   2 2002-10-30   L        98               106       41        87   
17      2   2 2002-10-30   W       100                86       39        71   
11      2   2 2002-10-30   L        90               102       35        85   
...    ..  ..        ...  ..       ...               ...      ...       ...   
46459  82  82 2023-04-09   W       120               114       42        89   
46458  82  82 2023-04-09   L       114               120       44        97   
46484  82  82 2023-04-09   L       117               128       51       101   
46469  82  82 2023-04-09   W       128               117       47        97   
46485  82  82 2023-04-09   L       109               114       41        97   

       team_FG%  team_3P  ...  Opp_ORL  Opp_PHI  Opp_PHO  Opp_POR  Opp_SAC  \
18        0.360        5  ...        0        0        0        0        0   
3         0.429        0  ...        0        0        0        0        0   
22        0.471        6  ...        0        0        0        0        0   
17        0.549        8  ...        0        0        0        0        0   
11        0.412        6  ...        0        0        0        1        0   
...         ...      ...  ...      ...      ...      ...      ...      ...   
46459     0.472       25  ...        0        0        0        0        0   
46458     0.454       11  ...        0        0        0        0        0   
46484     0.505       10  ...        0        0        0        0        0   
46469     0.485       18  ...        0        0        0        0        0   
46485     0.423       14  ...        0        0        0        0        0   

       Opp_SAS  Opp_SEA  Opp_TOR  Opp_UTA  Opp_WAS  
18           0        0        0        0        0  
3            0        0        0        0        0  
22           0        0        0        0        0  
17           0        0        0        0        0  
11           0        0        0        0        0  
...        ...      ...      ...      ...      ...  
46459        0        0        0        0        0  
46458        0        0        0        0        0  
46484        0        0        0        0        0  
46469        0        0        0        1        0  
46485        0        0        0        0        0  

[46486 rows x 146 columns]

In [ ]:
data.rename(columns={'Unnamed: 3_level_1': 'home_or_away'}, inplace=True)


In [ ]:
gamelog_data_1.rename(columns={'Opp.1': 'Opp_score'}, inplace=True)

In [ ]:
data.rename(columns={'Tm': 'Tm_score'}, inplace=True)

In [ ]:
data['Date'] = pd.to_datetime(data['Date'])

data.sort_values(by='Date', inplace=True)

In [ ]:
data['Date'] = pd.to_datetime(data['Date'])
data.sort_values(by='Date', inplace=True)
columns_to_aggregate = [
    'Tm_score', 'Opp_score', 'team_FG', 'team_FGA', 'team_FG%', 'team_3P', 'team_3PA',
    'team_3P%', 'team_FT', 'team_FTA', 'team_FT%', 'team_ORB', 'team_TRB',
    'team_AST', 'team_STL', 'team_BLK', 'team_TOV', 'team_PF',
    'opponent_FG', 'opponent_FGA', 'opponent_FG%', 'opponent_3P', 'opponent_3PA',
    'opponent_3P%', 'opponent_FT', 'opponent_FTA', 'opponent_FT%', 'opponent_ORB',
    'opponent_TRB', 'opponent_AST', 'opponent_STL', 'opponent_BLK', 'opponent_TOV',
    'opponent_PF']
window_size = 5
for col in columns_to_aggregate:
    shifted_data = data.groupby('team_name')[col].shift(1)
    data[f'{col}_rolling_avg'] = shifted_data.groupby(data['team_name']).rolling(window_size, min_periods=1).mean().reset_index(level=0, drop=True)


In [ ]:

def determine_season(date):
    year = date.year
    if date.month >= 10:
        return f'{year}-{year + 1}'
    else:
        return f'{year - 1}-{year}'
data['Season'] = data['Date'].apply(determine_season)

print(data.head())

       Rk  G       Date home_or_away  Opp W/L  Tm_score  Opp_score  team_FG  \
9163    1  1 2002-10-29            @  SAC   L        67         94       27   
10311   1  1 2002-10-29          NaN  PHI   W        95         88       36   
10721   1  1 2002-10-29            @  LAL   W        87         82       26   
10393   1  1 2002-10-29            @  ORL   L        88         95       31   
10639   1  1 2002-10-29          NaN  CLE   W        94         67       36   

       team_FGA  ...  opponent_FTA_rolling_avg  opponent_FT%_rolling_avg  \
9163         83  ...                       NaN                       NaN   
10311        81  ...                       NaN                       NaN   
10721        71  ...                       NaN                       NaN   
10393        78  ...                       NaN                       NaN   
10639        80  ...                       NaN                       NaN   

       opponent_ORB_rolling_avg  opponent_TRB_rolling_avg  \
9163   

In [ ]:
data['W/L_encoded'] = data['W/L'].apply(lambda x: 1 if x == 'W' else 0)

In [ ]:
data['W/L_encoded'] = data['W/L'].apply(lambda x: 1 if x == 'W' else 0)

In [ ]:

data.sort_values(by=['Season', 'Rk'], inplace=True)

training_data = data[data['Rk'] <= 62]
testing_data = data[(data['Rk'] > 62) & (data['Rk'] <= 79)]



In [ ]:
data.rename(columns={'Opp_score_rolling_avg': 'opponent_score_rolling_avg'}, inplace=True)

In [ ]:
data.rename(columns={'Tm_score_rolling_avg': 'team_score_rolling_avg'}, inplace=True)

In [ ]:
nan_counts_features = data[feature_columns].isnull().sum()
print(nan_counts_features)

Tm_score_rolling_avg        0
Opp_score_rolling_avg       0
team_FG_rolling_avg         0
team_FGA_rolling_avg        0
team_FG%_rolling_avg        0
team_3P_rolling_avg         0
team_3PA_rolling_avg        0
team_3P%_rolling_avg        0
team_FT_rolling_avg         0
team_FTA_rolling_avg        0
team_FT%_rolling_avg        0
team_ORB_rolling_avg        0
team_TRB_rolling_avg        0
team_AST_rolling_avg        0
team_STL_rolling_avg        0
team_BLK_rolling_avg        0
team_TOV_rolling_avg        0
team_PF_rolling_avg         0
opponent_FG_rolling_avg     0
opponent_FGA_rolling_avg    0
opponent_FG%_rolling_avg    0
opponent_3P_rolling_avg     0
opponent_3PA_rolling_avg    0
opponent_3P%_rolling_avg    0
opponent_FT_rolling_avg     0
opponent_FTA_rolling_avg    0
opponent_FT%_rolling_avg    0
opponent_ORB_rolling_avg    0
opponent_TRB_rolling_avg    0
opponent_AST_rolling_avg    0
opponent_STL_rolling_avg    0
opponent_BLK_rolling_avg    0
opponent_TOV_rolling_avg    0
opponent_P

In [ ]:
testing_data.columns

Index(['Rk', 'G', 'Date', 'W/L', 'Tm_score', 'Opp_score', 'team_FG',
       'team_FGA', 'team_FG%', 'team_3P',
       ...
       'Opp_ORL', 'Opp_PHI', 'Opp_PHO', 'Opp_POR', 'Opp_SAC', 'Opp_SAS',
       'Opp_SEA', 'Opp_TOR', 'Opp_UTA', 'Opp_WAS'],
      dtype='object', length=141)

In [ ]:
def calculate_winning_streak(s):
    streak = 0
    streaks = [0]
    for i in range(1, len(s)):
        if s.iloc[i-1] == 'W':
            streak += 1
        else:
            streak = 0
        streaks.append(streak)
    return streaks

data['winning_streak'] = data.groupby('team_name')['W/L'].transform(calculate_winning_streak)



In [ ]:
data.sort_values(by=['team_name', 'Date'], inplace=True)
data['game_date'] = pd.to_datetime(data['Date'])
data['prev_game_date'] = data.groupby('team_name')['game_date'].shift(1)
data['days_since_last_game'] = (data['game_date'] - data['prev_game_date']).dt.days
data['back_to_back'] = (data['days_since_last_game'] == 1).astype(int)


KeyError: 'team_name'

In [ ]:
data

Rk   G        Date W/L  Tm_score  Opposition_score  team_FG  team_FGA  \
0       2   2  2002-10-31   W       105                98       39        76   
1       2   2  2002-10-31   L        69               114       24        81   
2       2   2  2002-11-01   W        84                79       33        70   
3       2   2  2002-10-30   W        98                96       36        84   
4       2   2  2002-11-02   W        97                83       34        78   
...    ..  ..         ...  ..       ...               ...      ...       ...   
46481  82  82  2023-04-09   L        95               109       37        85   
46482  82  82  2023-04-09   W       138               117       51       104   
46483  82  82  2023-04-09   W       121               105       48        95   
46484  82  82  2023-04-09   L       117               128       51       101   
46485  82  82  2023-04-09   L       109               114       41        97   

       team_FG%  team_3P  ...  Opp_ORL  Opp_PHI  Opp_PHO  Opp_POR  Opp_SAC  \
0         0.513        3  ...        0        0        0        0        0   
1         0.296        7  ...        0        0        0        0        0   
2         0.471        3  ...        0        0        0        0        0   
3         0.429        0  ...        0        0        0        0        0   
4         0.436        9  ...        0        0        1        0        0   
...         ...      ...  ...      ...      ...      ...      ...      ...   
46481     0.435       11  ...        0        0        0        0        0   
46482     0.490       15  ...        0        0        0        0        0   
46483     0.505       11  ...        0        0        0        0        0   
46484     0.505       10  ...        0        0        0        0        0   
46485     0.423       14  ...        0        0        0        0        0   

       Opp_SAS  Opp_SEA  Opp_TOR  Opp_UTA  Opp_WAS  
0            0        0        0        1        0  
1            0        0        0        0        1  
2            0        0        0        0        0  
3            0        0        0        0        0  
4            0        0        0        0        0  
...        ...      ...      ...      ...      ...  
46481        0        0        0        0        0  
46482        0        0        0        0        0  
46483        0        0        0        0        0  
46484        0        0        0        0        0  
46485        0        0        0        0        0  

[46486 rows x 146 columns]

In [ ]:
import pandas as pd
data['home_or_away'] = data['home_or_away'].fillna('home')


In [ ]:
data_subset=Position_data[['team_name', 'home_or_away', 'player_GmSc', 'Pos']]
data_subset

NameError: name 'Position_data' is not defined

In [ ]:
import pandas as pd
data.rename(columns={'Opp_score': 'Opposition_score'}, inplace=True)


In [ ]:
import pandas as pd
def convert_season_format(season):
    if isinstance(season, str) and '-' in season:
        parts = season.split('-')
        if len(parts) == 2 and len(parts[1]) == 2:
            parts[1] = '20' + parts[1]
            return '-'.join(parts)
    return season
data['Season'] = data['Season'].apply(convert_season_format)




KeyError: 'Season'

In [ ]:
data.columns


Index(['Rk', 'G', 'Date', 'W/L', 'Tm_score', 'Opp_score', 'team_FG',
       'team_FGA', 'team_FG%', 'team_3P',
       ...
       'Opp_PHI', 'Opp_PHO', 'Opp_POR', 'Opp_SAC', 'Opp_SAS', 'Opp_SEA',
       'Opp_TOR', 'Opp_UTA', 'Opp_WAS', 'Rest_Days'],
      dtype='object', length=147)

In [ ]:
data = pd.get_dummies(data, columns=['home_or_away', 'team_name', 'Opp'])

In [ ]:
import pandas as pd
data['Date'] = pd.to_datetime(data['Date'])
data.sort_values(by='Date', inplace=True)
data['Rest_Days'] = None
last_game_date = {}
team_columns = [col for col in data.columns if col.startswith('team_name_')]

for index, row in data.iterrows():
    for team_col in team_columns:
        if row[team_col] == 1:
            team_name = team_col

            if team_name in last_game_date:

                rest_days = (row['Date'] - last_game_date[team_name]).days - 1
                data.at[index, 'Rest_Days'] = rest_days
            else:

                data.at[index, 'Rest_Days'] = None
            last_game_date[team_name] = row['Date']
            break


In [ ]:

original_feature_columns = ['team_score_rolling_avg',
       'opponent_score_rolling_avg', 'team_FG_rolling_avg', 'team_FGA_rolling_avg',
       'team_FG%_rolling_avg', 'team_3P_rolling_avg', 'team_3PA_rolling_avg',
       'team_3P%_rolling_avg', 'team_FT_rolling_avg', 'team_FTA_rolling_avg',
       'team_FT%_rolling_avg', 'team_ORB_rolling_avg', 'team_TRB_rolling_avg',
       'team_AST_rolling_avg', 'team_STL_rolling_avg', 'team_BLK_rolling_avg',
       'team_TOV_rolling_avg', 'team_PF_rolling_avg',
       'opponent_FG_rolling_avg', 'opponent_FGA_rolling_avg',
       'opponent_FG%_rolling_avg', 'opponent_3P_rolling_avg',
       'opponent_3PA_rolling_avg', 'opponent_3P%_rolling_avg',
       'opponent_FT_rolling_avg', 'opponent_FTA_rolling_avg',
       'opponent_FT%_rolling_avg', 'opponent_ORB_rolling_avg',
       'opponent_TRB_rolling_avg', 'opponent_AST_rolling_avg',
       'opponent_STL_rolling_avg', 'opponent_BLK_rolling_avg',
       'opponent_TOV_rolling_avg', 'opponent_PF_rolling_avg', 'back_to_back']

data.dropna(subset=original_feature_columns, inplace=True)

new_feature_columns = original_feature_columns + list(data.columns[data.columns.str.startswith('home_or_away_')]) \
 + list(data.columns[data.columns.str.startswith('team_name_')]) \
                      + list(data.columns[data.columns.str.startswith('Opp_')])

new_feature_columns = [col for col in new_feature_columns if col != 'Opp_score']

In [ ]:
new_feature_columns

['team_score_rolling_avg',
 'opponent_score_rolling_avg',
 'team_FG_rolling_avg',
 'team_FGA_rolling_avg',
 'team_FG%_rolling_avg',
 'team_3P_rolling_avg',
 'team_3PA_rolling_avg',
 'team_3P%_rolling_avg',
 'team_FT_rolling_avg',
 'team_FTA_rolling_avg',
 'team_FT%_rolling_avg',
 'team_ORB_rolling_avg',
 'team_TRB_rolling_avg',
 'team_AST_rolling_avg',
 'team_STL_rolling_avg',
 'team_BLK_rolling_avg',
 'team_TOV_rolling_avg',
 'team_PF_rolling_avg',
 'opponent_FG_rolling_avg',
 'opponent_FGA_rolling_avg',
 'opponent_FG%_rolling_avg',
 'opponent_3P_rolling_avg',
 'opponent_3PA_rolling_avg',
 'opponent_3P%_rolling_avg',
 'opponent_FT_rolling_avg',
 'opponent_FTA_rolling_avg',
 'opponent_FT%_rolling_avg',
 'opponent_ORB_rolling_avg',
 'opponent_TRB_rolling_avg',
 'opponent_AST_rolling_avg',
 'opponent_STL_rolling_avg',
 'opponent_BLK_rolling_avg',
 'opponent_TOV_rolling_avg',
 'opponent_PF_rolling_avg',
 'back_to_back',
 'home_or_away_@',
 'home_or_away_home']

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader, TensorDataset
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, roc_auc_score

target_column = 'W/L_encoded'
scaler = StandardScaler()
X_train = training_data[new_feature_columns]
y_train = training_data['W/L_encoded']
X_test = testing_data[new_feature_columns]
y_test = testing_data['W/L_encoded']
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train_tensor = torch.tensor(X_train_scaled, dtype=torch.float32)
y_train_tensor = torch.tensor(y_train.values, dtype=torch.float32)
X_test_tensor = torch.tensor(X_test_scaled, dtype=torch.float32)
y_test_tensor = torch.tensor(y_test.values, dtype=torch.float32)
train_dataset = TensorDataset(X_train_tensor, y_train_tensor)
test_dataset = TensorDataset(X_test_tensor, y_test_tensor)
train_loader = DataLoader(train_dataset, batch_size=64, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=64, shuffle=False)
class NBAPredictionModel(nn.Module):
    def __init__(self):
        super(NBAPredictionModel, self).__init__()
        self.fc1 = nn.Linear(len(new_feature_columns), 256)
        self.bn1 = nn.BatchNorm1d(256)
        self.dropout = nn.Dropout(0.7)
        self.fc2 = nn.Linear(256, 128)
        self.bn2 = nn.BatchNorm1d(128)
        self.fc3 = nn.Linear(128, 64)
        self.bn3 = nn.BatchNorm1d(64)
        self.fc4 = nn.Linear(64, 32)
        self.bn4 = nn.BatchNorm1d(32)
        self.fc5 = nn.Linear(32, 1)

    def forward(self, x):
        x = F.relu(self.bn1(self.fc1(x)))
        x = self.dropout(x)
        x = F.relu(self.bn2(self.fc2(x)))
        x = F.relu(self.bn3(self.fc3(x)))
        x = self.dropout(x)
        x = F.relu(self.bn4(self.fc4(x)))
        x = torch.sigmoid(self.fc5(x))
        return x

model = NBAPredictionModel()
criterion = nn.BCELoss()
optimizer = torch.optim.Adam(model.parameters(), lr=0.001)  # Adjusted as per tuning

num_epochs = 10
for epoch in range(num_epochs):
    model.train()
    for inputs, labels in train_loader:
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs.squeeze(), labels)
        loss.backward()
        optimizer.step()

    print(f'Epoch {epoch+1}/{num_epochs}, Loss: {loss.item()}')

model.eval()
true_labels = []
predictions = []
with torch.no_grad():
    for inputs, labels in test_loader:
        outputs = model(inputs).squeeze()
        predicted = (outputs > 0.5).float()
        true_labels.extend(labels.numpy())
        predictions.extend(predicted.numpy())

accuracy = accuracy_score(true_labels, predictions)
precision = precision_score(true_labels, predictions)
recall = recall_score(true_labels, predictions)
f1 = f1_score(true_labels, predictions)
auc_roc = roc_auc_score(true_labels, predictions)

print(f'Accuracy: {accuracy:.4f}, Precision: {precision:.4f}, Recall: {recall:.4f}, F1 Score: {f1:.4f}, AUC-ROC: {auc_roc:.4f}')


Epoch 1/10, Loss: 0.6842455267906189
Epoch 2/10, Loss: 0.6394143104553223
Epoch 3/10, Loss: 0.6580927968025208
Epoch 4/10, Loss: 0.626554548740387
Epoch 5/10, Loss: 0.643752932548523
Epoch 6/10, Loss: 0.6239702105522156
Epoch 7/10, Loss: 0.653088390827179
Epoch 8/10, Loss: 0.5652386546134949
Epoch 9/10, Loss: 0.69882732629776
Epoch 10/10, Loss: 0.6727428436279297
Accuracy: 0.6428, Precision: 0.6339, Recall: 0.6852, F1 Score: 0.6585, AUC-ROC: 0.6426


Average Accuracy: 0.6278448354466326
Average Precision: 0.6392029346137689
Average Recall: 0.601257311747956
Average F1 Score: 0.6190802955477503


In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader, TensorDataset
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, roc_auc_score

target_column = 'W/L_encoded'
scaler = StandardScaler()
X_train = training_data[new_feature_columns]
y_train = training_data['W/L_encoded']
X_test = testing_data[new_feature_columns]
y_test = testing_data['W/L_encoded']
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train_tensor = torch.tensor(X_train_scaled, dtype=torch.float32)
y_train_tensor = torch.tensor(y_train.values, dtype=torch.float32)
X_test_tensor = torch.tensor(X_test_scaled, dtype=torch.float32)
y_test_tensor = torch.tensor(y_test.values, dtype=torch.float32)
train_dataset = TensorDataset(X_train_tensor, y_train_tensor)
test_dataset = TensorDataset(X_test_tensor, y_test_tensor)
train_loader = DataLoader(train_dataset, batch_size=64, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=64, shuffle=False)
class NBAPredictionModelEnhanced(nn.Module):
    def __init__(self):
        super(NBAPredictionModelEnhanced, self).__init__()
        self.fc1 = nn.Linear(len(new_feature_columns), 512)  # Increased size
        self.bn1 = nn.BatchNorm1d(512)
        self.fc2 = nn.Linear(512, 256)  # Increased size
        self.bn2 = nn.BatchNorm1d(256)
        self.fc3 = nn.Linear(256, 128)  # Increased size
        self.bn3 = nn.BatchNorm1d(128)
        self.fc4 = nn.Linear(128, 64)   # Keep or adjust based on performance
        self.bn4 = nn.BatchNorm1d(64)
        # New additional layer
        self.fc5 = nn.Linear(64, 32)
        self.bn5 = nn.BatchNorm1d(32)
        # Output layer remains the same
        self.fc6 = nn.Linear(32, 1)
        self.dropout = nn.Dropout(0.5)

    def forward(self, x):
        x = F.relu(self.bn1(self.fc1(x)))
        x = self.dropout(x)
        x = F.relu(self.bn2(self.fc2(x)))
        x = F.relu(self.bn3(self.fc3(x)))
        x = self.dropout(x)
        x = F.relu(self.bn4(self.fc4(x)))
        x = F.relu(self.bn5(self.fc5(x)))
        x = self.dropout(x)
        x = torch.sigmoid(self.fc6(x))
        return x

model = NBAPredictionModel()
criterion = nn.BCELoss()
optimizer = torch.optim.Adam(model.parameters(), lr=0.001)
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(optimizer, mode='min', factor=0.1, patience=3, verbose=True)

num_epochs = 20
for epoch in range(num_epochs):
    model.train()
    total_loss = 0
    for inputs, labels in train_loader:
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs.squeeze(), labels)
        loss.backward()
        optimizer.step()
        total_loss += loss.item()

    avg_loss = total_loss / len(train_loader)
    print(f'Epoch {epoch+1}/{num_epochs}, Loss: {avg_loss:.4f}')
    scheduler.step(avg_loss)
    model.eval()
    true_labels = []
    predictions = []
    with torch.no_grad():
        for inputs, labels in test_loader:
            outputs = model(inputs).squeeze()
            predicted = (outputs > 0.5).float()
            true_labels.extend(labels.numpy())
            predictions.extend(predicted.numpy())

    accuracy = accuracy_score(true_labels, predictions)
    precision = precision_score(true_labels, predictions)
    recall = recall_score(true_labels, predictions)
    f1 = f1_score(true_labels, predictions)
    auc_roc = roc_auc_score(true_labels, predictions)

    print(f'Accuracy: {accuracy:.4f}, Precision: {precision:.4f}, Recall: {recall:.4f}, F1 Score: {f1:.4f}, AUC-ROC: {auc_roc:.4f}')


Epoch 1/20, Loss: 0.6806
Accuracy: 0.6365, Precision: 0.6379, Recall: 0.6400, F1 Score: 0.6389, AUC-ROC: 0.6364
Epoch 2/20, Loss: 0.6608
Accuracy: 0.6397, Precision: 0.6423, Recall: 0.6387, F1 Score: 0.6405, AUC-ROC: 0.6397
Epoch 3/20, Loss: 0.6548
Accuracy: 0.6410, Precision: 0.6340, Recall: 0.6760, F1 Score: 0.6543, AUC-ROC: 0.6408
Epoch 4/20, Loss: 0.6524
Accuracy: 0.6425, Precision: 0.6354, Recall: 0.6773, F1 Score: 0.6557, AUC-ROC: 0.6423
Epoch 5/20, Loss: 0.6511
Accuracy: 0.6408, Precision: 0.6308, Recall: 0.6876, F1 Score: 0.6580, AUC-ROC: 0.6405
Epoch 6/20, Loss: 0.6499
Accuracy: 0.6424, Precision: 0.6386, Recall: 0.6648, F1 Score: 0.6514, AUC-ROC: 0.6423
Epoch 7/20, Loss: 0.6475
Accuracy: 0.6397, Precision: 0.6440, Recall: 0.6330, F1 Score: 0.6384, AUC-ROC: 0.6397
Epoch 8/20, Loss: 0.6477
Accuracy: 0.6376, Precision: 0.6168, Recall: 0.7361, F1 Score: 0.6712, AUC-ROC: 0.6370
Epoch 9/20, Loss: 0.6459
Accuracy: 0.6412, Precision: 0.6461, Recall: 0.6327, F1 Score: 0.6393, AUC-ROC:

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F

class RNN_CNN_Model(nn.Module):
    def __init__(self, num_features, hidden_dim_rnn, hidden_dim_cnn, output_dim=2):
        super(RNN_CNN_Model, self).__init__()
        self.rnn = nn.LSTM(input_size=num_features, hidden_size=hidden_dim_rnn, batch_first=True)

        self.conv1 = nn.Conv1d(in_channels=hidden_dim_rnn, out_channels=hidden_dim_cnn, kernel_size=3, stride=1, padding=1)

        self.fc1 = nn.Linear(hidden_dim_cnn * sequence_length, 64)
        self.output = nn.Linear(64, output_dim)

    def forward(self, x):
        r_out, (h_n, h_c) = self.rnn(x)
        r_out = r_out[:, :, :].contiguous()
        r_out = r_out.permute(0, 2, 1)
        c_out = F.relu(self.conv1(r_out))

        c_out = c_out.view(c_out.size(0), -1)
        fc_out = F.relu(self.fc1(c_out))
        output = self.output(fc_out)


model = RNN_CNN_Model(num_features=num_features, hidden_dim_rnn=128, hidden_dim_cnn=64, output_dim=2)

import torch.optim as optim
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=0.001)
epochs = 10
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model.to(device)

for epoch in range(epochs):
    model.train()
    running_loss = 0.0

    for inputs, labels in train_loader:
        inputs, labels = inputs.to(device), labels.to(device)
        optimizer.zero_grad()

        # Forward pass
        outputs = model(inputs)
        loss = criterion(outputs, labels.long())
        loss.backward()
        optimizer.step()

        running_loss += loss.item()

    print(f'Epoch {epoch+1}, Loss: {running_loss/len(train_loader)}')
    model.eval()
    val_loss = 0.0
    correct = 0
    total = 0

    with torch.no_grad():
        for inputs, labels in val_loader:
            inputs, labels = inputs.to(device), labels.to(device)
            outputs = model(inputs)
            loss = criterion(outputs, labels.long())
            val_loss += loss.item()

            _, predicted = torch.max(outputs.data, 1)
            total += labels.size(0)
            correct += (predicted == labels).sum().item()

    print(f'Validation Loss: {val_loss/len(val_loader)}, Accuracy: {correct/total*100}%')





Epoch 1, Loss: 0.6904780829835061
Validation Loss: 0.688039388150385, Accuracy: 54.415402818113364%
Epoch 2, Loss: 0.6816436783787305
Validation Loss: 0.691062768844709, Accuracy: 53.7377648703883%
Epoch 3, Loss: 0.6564196746238538
Validation Loss: 0.7161824421523368, Accuracy: 51.78014413251587%
Epoch 4, Loss: 0.590064053640103
Validation Loss: 0.744482105725432, Accuracy: 51.69409486931268%
Epoch 5, Loss: 0.5093373418777617
Validation Loss: 0.7715683812147951, Accuracy: 51.40367860600193%
Epoch 6, Loss: 0.46216050180223434
Validation Loss: 0.782082785074025, Accuracy: 50.82284607938045%
Epoch 7, Loss: 0.43672031718153964
Validation Loss: 0.7814439004414702, Accuracy: 51.69409486931268%
Epoch 8, Loss: 0.4212393592946911
Validation Loss: 0.7799301245441176, Accuracy: 51.737119500914275%
Epoch 9, Loss: 0.41611467140266695
Validation Loss: 0.7878160991080819, Accuracy: 51.08099386899%
Epoch 10, Loss: 0.4099505760173174
Validation Loss: 0.7894874386591454, Accuracy: 51.33914165859955%


In [ ]:
print("Shape of outputs:", outputs.shape)
print("Shape of labels:", labels.shape)

Shape of outputs: torch.Size([64, 1])
Shape of labels: torch.Size([64])


In [ ]:
print("Minimum value of outputs:", outputs.min())
print("Maximum value of outputs:", outputs.max())

Minimum value of outputs: tensor(nan, grad_fn=<MinBackward1>)
Maximum value of outputs: tensor(nan, grad_fn=<MaxBackward1>)
